# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model loaded [A2C]

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 517, done.
remote: Counting objects: 100% (124/124), done.
remote: Compressing objects: 100% (59/59), done.
remote: Total 517 (delta 65), reused 121 (delta 64), pack-reused 393
Receiving objects: 100% (517/517), 188.99 MiB | 25.30 MiB/s, done.
Resolving deltas: 100% (214/214), done.
Checking out files: 100% (223/223), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          RL_VPP_Thesis/
Algorithm_simulator_notebooks/    trained_models/
data/                             VPP_environment.py
EV_experiment_notebooks/          VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  wandb/
README.md


In [ ]:
import yaml
import numpy as np
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from stable_baselines3 import A2C #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')
wandb, version 0.13.4


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f043f7634d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
#env.plot_VPP_input_data()

Charging event: 1, Arrival time: 2022-01-01 05:45:00, Parking_time: 22.869064351048774, Leaving_time: 2022-01-02 04:37:08.631664, SOC: 0.544957906093075, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 1043, Arrival time: 2022-12-31 15:15:00, Parking_time: 21.81220607158969, Leaving_time: 2023-01-01 13:03:43.941858, SOC: 0.24341448706912433, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -21214.64 , Grid_used_en=kWh  4947.18 , RE-to-vehicle_unused_en=kWh  -26161.81 , Total_selling_cost=€  -489.75 , Grid_cost=€  233.11
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  20613.48 , Grid_used_en=kWh  37928.71 , RE-to-vehicle_unused_en=kWh  17315.23 , Total_selling_cost=€  868.19 , Grid_cost=€  1351.29 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08


In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22231.71 , Grid_used_en=kWh  39383.4 , RE-to-vehicle_unused_en=kWh  17151.69 , Total_selling_cost=€  906.69 , Grid_cost=€  1400.15 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/A2C_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/A2C_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="Simulator_notebooks/A2C_VPP_simulator.ipynb"


In [ ]:
#Loading training model, from local directory or from wandb previous trainings
A2C_path = "trained_models/A2C_models/model_A2C_"

model_id = "1u6pwi97"
model = A2C.load(A2C_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21499.36 , Grid_used_en=kWh  38830.25 , RE-to-vehicle_unused_en=kWh  17330.89 , Total_selling_cost=€  903.14 , Grid_cost=€  1389.37 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6336.23 , Grid_used_en=KWh  6549.34 , RE-to-vehicle_unused_en=KWh  12885.57 , Total_selling_cost=€  -90.7 , Grid_cost=€  232.04 
 EV_INFO: Av.EV_energy_leaving=kWh  64.83 , Std.EV_energy_leaving=kWh  34.09 , EV_departures =  1042 , EV_queue_left =  0
SCORE:  Cumulative_reward= 159089.06 - Step_rewars (load_t= 192158.63, EVs_energy_t= -31123.57)
 - Final_rewards (Av.EVs_energy= 13647.73, Grid_used_en= -6068.0, RE-to-vehicle_unused_en= -10190.68, Grid_cost= 664.95)
Episode:1 Score:159089.05933477497


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0    1    2          3           EVs_id       actions  \
time                                                                           
2022-01-01 00:00:00  0.0  0.0  0.0   0.000000     [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  0.0  0.0  0.0   0.000000     [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:30:00  0.0  0.0  0.0   0.000000     [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:45:00  0.0  0.0  0.0   0.000000     [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 01:00:00  0.0  0.0  0.0   0.000000     [0, 0, 0, 0]  [1, 2, 2, 1]   
...                  ...  ...  ...        ...              ...           ...   
2022-06-06 04:45:00  0.0  0.0  0.0  99.989998  [0, 0, 0, 2521]  [2, 2, 2, 1]   
2022-06-06 05:00:00  0.0  0.0  0.0  99.989998  [0, 0, 0, 2521]  [2, 2, 2, 1]   
2022-06-06 05:15:00  0.0  0.0  0.0  99.989998  [0, 0, 0, 2521]  [2, 2, 2, 1]   
2022-06-06 05:30:00  0.0  0.0  0.0  99.989998  [0, 0, 0, 2521]  [2, 2, 2, 1]   
2022-06-06 05:45:00  0.0  0.0  0.0  99.989998  [0, 0, 0, 2521]  [2, 2, 2, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00  [False, False, False, False]        0.000000   
2022-01-01 00:30:00  [False, False, False, False]        0.000000   
2022-01-01 00:45:00  [False, False, False, False]        0.000000   
2022-01-01 01:00:00  [False, False, False, False]        0.000000   
...                                           ...             ...   
2022-06-06 04:45:00   [False, False, False, True]        0.000009   
2022-06-06 05:00:00   [False, False, False, True]        0.000009   
2022-06-06 05:15:00   [False, False, False, True]        0.000009   
2022-06-06 05:30:00   [False, False, False, True]        0.000009   
2022-06-06 05:45:00   [False, False, False, True]        0.000009   

                     ev_discharged_pwr       load  load_reward  EV_reward  \
time                                                                        
2022-01-01 00:00:00                0.0   1.211512    -5.358441        0.0   
2022-01-01 00:15:00                0.0   3.774805    -2.744177        0.0   
2022-01-01 00:30:00                0.0   2.146506    -1.994207        0.0   
2022-01-01 00:45:00                0.0   1.696524    -2.386579        0.0   
2022-01-01 01:00:00                0.0   1.931947    -1.675911        0.0   
...                                ...        ...          ...        ...   
2022-06-06 04:45:00                0.0  -8.440217   -12.736251        0.0   
2022-06-06 05:00:00                0.0 -12.509876   -13.037878        0.0   
2022-06-06 05:15:00                0.0 -12.841665   -12.975085        0.0   
2022-06-06 05:30:00                0.0 -12.772593   -11.614462        0.0   
2022-06-06 05:45:00                0.0 -11.275908   -12.000544        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -5.358441  
2022-01-01 00:15:00  -2.744177  
2022-01-01 00:30:00  -1.994207  
2022-01-01 00:45:00  -2.386579  
2022-01-01 01:00:00  -1.675911  
...                        ...  
2022-06-06 04:45:00 -12.736251  
2022-06-06 05:00:00 -13.037878  
2022-06-06 05:15:00 -12.975085  
2022-06-06 05:30:00 -11.614462  
2022-06-06 05:45:00 -12.000544  

[15000 rows x 13 columns]

In [ ]:
#env.plot_Elvis_results()

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 3130, Arrival time: 2022-01-01 11:30:00, Parking_time: 24, Leaving_time: 2022-01-02 11:30:00, SOC: 0.5259141466212002, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 4172, Arrival time: 2023-01-01 00:00:00, Parking_time: 24, Leaving_time: 2023-01-02 00:00:00, SOC: 0.36522042815302513, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en=kWh  2136.67 , RE-to-vehicle_unused_en=kWh  -32222.06 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13782.27 , Grid_used_en=kWh  35262.49 , RE-to-vehicle_unused_en=kWh  21480.22 , Total_selling_cost=€  645.48 , Grid_cost=€  1532.67 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_VPP_input_data()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13658.29 , Grid_used_en=kWh  35476.96 , RE-to-vehicle_unused_en=kWh  21818.67 , Total_selling_cost=€  652.95 , Grid_cost=€  1548.52 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....


In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = A2C.load(A2C_path + model_id, env=env)

In [ ]:
#Validating Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  11415.15 , Grid_used_en=kWh  33561.7 , RE-to-vehicle_unused_en=kWh  22146.55 , Total_selling_cost=€  598.75 , Grid_cost=€  1497.08 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -13647.44 , Grid_used_en=KWh  3251.31 , RE-to-vehicle_unused_en=KWh  16898.76 , Total_selling_cost=€  -536.08 , Grid_cost=€  144.1 
 EV_INFO: Av.EV_energy_leaving=kWh  66.53 , Std.EV_energy_leaving=kWh  33.04 , EV_departures =  1042 , EV_queue_left =  0
SCORE:  Cumulative_reward= 166890.68 - Step_rewars (load_t= 193508.15, EVs_energy_t= -26041.19)
 - Final_rewards (Av.EVs_energy= 11406.51, Grid_used_en= -3137.78, RE-to-vehicle_unused_en= -10557.05, Grid_cost= 1712.04)
Episode:1 Score:166890.68306601234


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0    1          2    3           EVs_id       actions  \
time                                                                           
2022-01-01 00:00:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:15:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:30:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:45:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 01:00:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 0, 1, 0]   
...                  ...  ...        ...  ...              ...           ...   
2022-06-06 04:45:00  0.0  0.0  57.317509  0.0  [0, 0, 5663, 0]  [0, 0, 1, 0]   
2022-06-06 05:00:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 1, 1, 2]   
2022-06-06 05:15:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-06-06 05:30:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-06-06 05:45:00  0.0  0.0   0.000000  0.0     [0, 0, 0, 0]  [0, 0, 1, 0]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00    [True, True, False, True]        0.000000   
2022-01-01 00:15:00    [True, True, False, True]        0.000000   
2022-01-01 00:30:00    [True, True, False, True]        0.000000   
2022-01-01 00:45:00    [True, True, False, True]        0.000000   
2022-01-01 01:00:00    [True, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00     [True, True, True, True]       10.816603   
2022-06-06 05:00:00  [True, False, False, False]       11.000000   
2022-06-06 05:15:00    [True, True, False, True]        0.000000   
2022-06-06 05:30:00    [True, True, False, True]        0.000000   
2022-06-06 05:45:00    [True, True, False, True]        0.000000   

                     ev_discharged_pwr       load  load_reward  EV_reward  \
time                                                                        
2022-01-01 00:00:00                0.0  -3.089386    -4.923251   0.000000   
2022-01-01 00:15:00                0.0  -3.953950    -5.255998   0.000000   
2022-01-01 00:30:00                0.0  -4.281598    -4.076976   0.000000   
2022-01-01 00:45:00                0.0  -3.446185    -4.039026   0.000000   
2022-01-01 01:00:00                0.0  -3.423416    -5.376507   0.000000   
...                                ...        ...          ...        ...   
2022-06-06 04:45:00                0.0   0.000000    -4.074847   7.820666   
2022-06-06 05:00:00                0.0  -3.444908   -14.400642   0.000000   
2022-06-06 05:15:00                0.0 -14.340706   -13.609212   0.000000   
2022-06-06 05:30:00                0.0 -13.470134   -14.324501   0.000000   
2022-06-06 05:45:00                0.0 -14.256951   -15.461808   0.000000   

                       rewards  
time                            
2022-01-01 00:00:00  -4.923251  
2022-01-01 00:15:00  -5.255998  
2022-01-01 00:30:00  -4.076976  
2022-01-01 00:45:00  -4.039026  
2022-01-01 01:00:00  -5.376507  
...                        ...  
2022-06-06 04:45:00   3.745820  
2022-06-06 05:00:00 -14.400642  
2022-06-06 05:15:00 -13.609212  
2022-06-06 05:30:00 -14.324501  
2022-06-06 05:45:00 -15.461808  

[15000 rows x 13 columns]

In [ ]:
#env.plot_Elvis_results()

In [ ]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 6259, Arrival time: 2022-01-01 11:30:00, Parking_time: 24, Leaving_time: 2022-01-02 11:30:00, SOC: 0.4359902076915005, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 7301, Arrival time: 2022-12-31 18:45:00, Parking_time: 24, Leaving_time: 2023-01-01 18:45:00, SOC: 0.4549364380449978, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , Grid_used_en=kWh  1556.25 , RE-to-vehicle_unused_en=kWh  -35673.95 , Total_selling_cost=€  -1196.64 , Grid_cost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  10043.47 , Grid_used_en=kWh  33381.08 , RE-to-vehicle_unused_en=kWh  23337.61 , Total_selling_cost=€  537.19 , Grid_cost=€  1405.42 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_VPP_input_data()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  9793.89 , Grid_used_en=kWh  32606.29 , RE-to-vehicle_unused_en=kWh  22812.41 , Total_selling_cost=€  529.53 , Grid_cost=€  1363.02 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....


In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = A2C.load(A2C_path + model_id, env=env)

In [ ]:
#Training Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8349.93 , Grid_used_en=kWh  31804.2 , RE-to-vehicle_unused_en=kWh  23454.26 , Total_selling_cost=€  440.56 , Grid_cost=€  1306.61 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -16815.27 , Grid_used_en=KWh  2620.12 , RE-to-vehicle_unused_en=KWh  19435.39 , Total_selling_cost=€  -573.28 , Grid_cost=€  115.68 
 EV_INFO: Av.EV_energy_leaving=kWh  67.04 , Std.EV_energy_leaving=kWh  33.38 , EV_departures =  1039 , EV_queue_left =  0
SCORE:  Cumulative_reward= 140939.05 - Step_rewars (load_t= 168547.14, EVs_energy_t= -26380.96)
 - Final_rewards (Av.EVs_energy= 9927.77, Grid_used_en= -2546.24, RE-to-vehicle_unused_en= -11787.2, Grid_cost= 3178.55)
Episode:1 Score:140939.05478524667


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(14995)

0    1          2          3  \
time                                                        
2022-01-01 00:00:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:15:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:30:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:45:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 01:00:00   0.000000  0.0   0.000000   0.000000   
...                        ...  ...        ...        ...   
2022-06-06 03:30:00  47.163662  0.0  55.995556  79.698380   
2022-06-06 03:45:00  47.853821  0.0  55.745556  80.388535   
2022-06-06 04:00:00  48.959671  0.0  55.495556  81.494385   
2022-06-06 04:15:00  50.027504  0.0  55.245556  82.562218   
2022-06-06 04:30:00  50.826153  0.0  54.995556  83.360870   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
...                                    ...           ...   
2022-06-06 03:30:00  [8779, 0, 8778, 8777]  [1, 2, 2, 1]   
2022-06-06 03:45:00  [8779, 0, 8778, 8777]  [1, 2, 2, 1]   
2022-06-06 04:00:00  [8779, 0, 8778, 8777]  [1, 2, 2, 1]   
2022-06-06 04:15:00  [8779, 0, 8778, 8777]  [1, 2, 2, 1]   
2022-06-06 04:30:00  [8779, 0, 8778, 8777]  [1, 2, 2, 1]   

                                     mask_truth  ev_charged_pwr  \
time                                                              
2022-01-01 00:00:00   [True, True, False, True]        0.000000   
2022-01-01 00:15:00   [True, True, False, True]        0.000000   
2022-01-01 00:30:00   [True, True, False, True]        0.000000   
2022-01-01 00:45:00   [True, True, False, True]        0.000000   
2022-01-01 01:00:00   [True, True, False, True]        0.000000   
...                                         ...             ...   
2022-06-06 03:30:00  [True, False, False, True]        4.371759   
2022-06-06 03:45:00  [True, False, False, True]        5.521266   
2022-06-06 04:00:00  [True, False, False, True]        8.846793   
2022-06-06 04:15:00  [True, False, False, True]        8.542650   
2022-06-06 04:30:00  [True, False, False, True]        6.389199   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -2.895187e+00    -3.419887        0.0   
2022-01-01 00:15:00                0.0 -3.051932e+00    -3.947332        0.0   
2022-01-01 00:30:00                0.0 -3.368399e+00    -5.600173        0.0   
2022-01-01 00:45:00                0.0 -4.660190e+00    -6.147771        0.0   
2022-01-01 01:00:00                0.0 -5.262548e+00    -5.674384        0.0   
...                                ...           ...          ...        ...   
2022-06-06 03:30:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 03:45:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 04:00:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 04:15:00               -1.0  8.881784e-16    15.000000        0.0   
2022-06-06 04:30:00               -1.0  0.000000e+00    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -3.419887  
2022-01-01 00:15:00  -3.947332  
2022-01-01 00:30:00  -5.600173  
2022-01-01 00:45:00  -6.147771  
2022-01-01 01:00:00  -5.674384  
...                        ...  
2022-06-06 03:30:00  15.000000  
2022-06-06 03:45:00  15.000000  
2022-06-06 04:00:00  15.000000  
2022-06-06 04:15:00  15.000000  
2022-06-06 04:30:00  15.000000  

[14995 rows x 13 columns]

In [ ]:
#env.plot_Elvis_results()

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()